In [1]:
import cv2
import time
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline
import matplotlib
from IPython.display import Markdown as md
import os
import ipywidgets as wg
from IPython.display import display
from matplotlib import cm
import math
import json

from random import randint
from functions import *

In [10]:
videos_dir = "../Videos/"

frame_n = wg.Play(
    value=0,
    min=0,
    max=100,
    step=1,
    description="Press play",
    disabled=False
)
slider_range = wg.IntRangeSlider(
    value=[0, 100],
    min=0,
    max=100,
    step=1,
    description='Cut:',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d',
)
slider = wg.IntSlider(value=0,
    min=0,
    max=100,
    step=1,
    description='Frame:',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)
width_range = wg.IntRangeSlider(
    value=[0, 100],
    min=0,
    max=100,
    step=1,
    description='Width:',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d',
)
height_range = wg.IntRangeSlider(
    value=[0, 100],
    min=0,
    max=100,
    step=1,
    description='Heigth:',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d',
)
resolution = wg.IntSlider(value=0,
    min=0,
    max=480,
    step=1,
    description='Resolution:',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)

save_vid = wg.Button(description='Save Video')

wg.jslink((frame_n, 'value'), (slider, 'value'))

videos = os.listdir(videos_dir)
videos.append("None")
video_dropdown = wg.Dropdown( options=videos,
                        value='None',
                        description='Video:',
                        disabled=False)

output_name = wg.Text(
    value='',
    placeholder='File output',
    disabled=False
)

def on_value_change(change):
    slider.min, slider.max = slider_range.value[0], slider_range.value[1]

def on_video_change(change):
    cap = cv2.VideoCapture(videos_dir + video_dropdown.value)
    framewidth = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
    frameheight = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
    fps = int(cap.get(cv2.CAP_PROP_FPS))
    n_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
    frame_n.max = n_frames - 1
    slider.max = n_frames - 1
    slider_range.max = n_frames - 1
    slider_range.value = (0, n_frames - 1)
    height_range.max, width_range.max = frameheight, framewidth
    height_range.value, width_range.value = (0, frameheight), (0, framewidth)
    resolution.max = frameheight
    resolution.value = frameheight
    cap.release()

def on_res_change(change):
    cap = cv2.VideoCapture(videos_dir + video_dropdown.value)
    framewidth = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
    frameheight = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
    in_height = resolution.value
    in_width = int((in_height/frameheight)*framewidth)
    height_range.max, width_range.max = in_height, in_width
    height_range.value, width_range.value = (0, in_height), (0, in_width)
    cap.release()
    
def on_save_vid_clicked(b):
    if(output_name.value==''):
        print("Choose a file name", end="\r")
    else:
        output_path = videos_dir + output_name.value
        print("Saving video at: {}".format(output_path))
        edit_video(video_dropdown.value, 0, r = slider_range.value, x=width_range.value, 
                   y=height_range.value, in_height=resolution.value, 
                   save_vid=True, output_path=output_path)
    
slider_range.observe(on_value_change, names='value')    
video_dropdown.observe(on_video_change, names='value')
resolution.observe(on_res_change, names='value')
save_vid.on_click(on_save_vid_clicked)

y = wg.interactive_output(edit_video, {"video_name":video_dropdown, "n":frame_n, "r": slider_range,
                                       "x":width_range, "y":height_range, "in_height":resolution})

hbox1 = wg.HBox([video_dropdown, frame_n])
hbox2 = wg.VBox([output_name, save_vid])
vbox1 = wg.VBox([slider, slider_range, width_range, height_range, resolution, hbox2])
hbox3 = wg.HBox([y, vbox1])
vbox2 = wg.VBox([hbox1, hbox3])

display(vbox2)

In [22]:
t1 = wg.IntSlider(
    value=7,
    min=0,
    max=10,
    step=1,
    description='Test:',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)
tabs = ['P0', 'P1']
children = []
children.append(t1)
children.append(t1)
tab = wg.Tab()
tab.children = children
for i in range(len(children)):
        tab.set_title(i, tabs[i])
tab

In [18]:
def processVideo(input_video, threshold, n_interp_samples, paf_score_th, conf_th, summary, output_name):
    video_path = videos_dir + input_video
    video_name = (input_video).split(sep='.')[0]

    file_dir = data_dir + video_name + '/'
    if not os.path.exists(file_dir):
        os.makedirs(file_dir)

    if output_name.endswith(".json"):
        file_path = file_dir + output_name
    else:
        file_path = file_dir + output_name + '.json'
     
    if os.path.exists(file_path):
        print("File name already exists")
        return
    
    output_path = data_dir + video_name + "/" + output_name + ".mp4"

    cap = cv2.VideoCapture(video_path)

    length = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
    fps = int(cap.get(cv2.CAP_PROP_FPS))

    has_frame, image = cap.read()
    frame_width = image.shape[1]
    frame_height = image.shape[0]

    cap.set(2,0.0)

    file_metadata = {
        'video_name': video_name,
        'n_frames': length,
        'n_points': n_points,
        'frame_width': frame_width,
        'frame_height': frame_height,
        'summary': summary,
    }

    with open(file_path, 'w') as f:
        f.write(json.dumps(file_metadata))
        f.write('\n')

    fourcc = cv2.VideoWriter_fourcc(*'X264')
    vid_writer = cv2.VideoWriter(output_path, fourcc, fps, (image.shape[1],image.shape[0]))

    print("Processing...")

    for fn in range(length):
        t = time.time()

        has_frame, image = cap.read()

        output, _ = SingleFrameInference(image, print_time=False)

        # Gerar lista classificando os pontos para cada pessoa identificada
        personwise_keypoints, keypoints_list = processKeypoints(output, frame_width, frame_height,                                                                       threshold, n_interp_samples,                                                                             paf_score_th, conf_th)

        frame_clone = image.copy()

        for i in range(17):
            for n in range(len(personwise_keypoints)):
                index = personwise_keypoints[n][np.array(pose_pairs[i])]
                if -1 in index:
                    continue
                B = np.int32(keypoints_list[index.astype(int), 0])
                A = np.int32(keypoints_list[index.astype(int), 1])
                cv2.line(frame_clone, (B[0], A[0]), (B[1], A[1]), colors[i], 3, cv2.LINE_AA)

        vid_writer.write(frame_clone)

        file_data = {
            'output': output.tolist(),
            'keypoints_list': keypoints_list.tolist(),
            'personwise_keypoints': personwise_keypoints.tolist(),
            'angles': []   
        }

        with open(file_path, 'a') as f:
            f.write(json.dumps(file_data))
            f.write('\n')

        time_taken = time.time() - t
        print("                                                    ", end='\r')
        print("[{0:d}/{1:d}] {2:.1f} seconds/frame".format(fn+1, length, time_taken), end="\r")

    vid_writer.release()
    cap.release()
    print()
    print("Done")

In [4]:
threshold = 0.1
n_interp_samples = 10
paf_score_th = 0.1
conf_th = 0.7
summary = "pilot"
input_video = "Remo_Victor_500-503.mp4"
processVideo(input_video, threshold, n_interp_samples, paf_score_th, conf_th, summary)

Processing...
[50/50] 9.7 seconds/framee
Done


In [20]:
videos = os.listdir(videos_dir)
input_video = wg.Dropdown(options=videos,
                        value="Remo_Lite_480p.mp4",
                        description='Video:',
                        disabled=False)
model_nn = wg.Dropdown( options=["None", "Openpose Model"],
                        value="None",
                        description='Inference:',
                        disabled=False)
threshold = wg.FloatText(value=0.1, description='threshold:',disabled=False)
n_interp_samples = wg.IntText(value=10, description='n_interp_s:',disabled=False)
paf_score_th = wg.FloatText(value=0.1, description='paf_score_th:',disabled=False)
conf_th = wg.FloatText(value=0.7, description='conf_th:',disabled=False)
summary = wg.Text(value='',placeholder='description',description='Summary:',disabled=False)
output_name = wg.Text(
        value='',
        placeholder='File output name',
        description='Output:',
        disabled=False
    )
process_vid = wg.Button(description='Process Video')

def onProcessClicked(b):
    if(model_nn.value=='None'):
        print("Select inference method")
    elif(model_nn.value=='Openpose Model'):
        processVideo(input_video.value, threshold.value, n_interp_samples.value,
                     paf_score_th.value, conf_th.value, summary.value, output_name.value)
    else:
        print("Post processing not implemented yet")
        
process_vid.on_click(onProcessClicked)

vbox1 = wg.VBox([input_video, model_nn, threshold, n_interp_samples, paf_score_th, conf_th, summary, output_name, process_vid])
display(vbox1)

Select inference method
File name already exists
Processing...
[50/50] 10.9 seconds/frame                          
Done


In [8]:
import importlib
import functions
importlib.reload(functions)
from functions import *

In [ ]:
def processingInterface()
    videos = os.listdir(videos_dir)
    input_video = wg.Dropdown(options=videos,
                            value="Remo_Lite_480p.mp4",
                            description='Video:',
                            disabled=False)
    model_nn = wg.Dropdown( options=["None", "Openpose Model"],
                            value="None",
                            description='Inference:',
                            disabled=False)
    threshold = wg.FloatText(value=0.1, description='threshold:',disabled=False)
    n_interp_samples = wg.IntText(value=10, description='n_interp_s:',disabled=False)
    paf_score_th = wg.FloatText(value=0.1, description='paf_score_th:',disabled=False)
    conf_th = wg.FloatText(value=0.7, description='conf_th:',disabled=False)
    summary = wg.Text(value='',placeholder='description',description='Summary:',disabled=False)
    output_name = wg.Text(
            value='',
            placeholder='File output name',
            description='Output:',
            disabled=False
        )
    process_vid = wg.Button(description='Process Video')

    def onProcessClicked(b):
        if(model_nn.value=='None'):
            print("Select inference method")
        elif(model_nn.value=='Openpose Model'):
            processVideo(input_video.value, threshold.value, n_interp_samples.value,
                         paf_score_th.value, conf_th.value, summary.value, output_name.value)
        else:
            print("Post processing not implemented yet")

    process_vid.on_click(onProcessClicked)

    vbox1 = wg.VBox([input_video, model_nn, threshold, n_interp_samples, paf_score_th, conf_th, summary, output_name, process_vid])
    return vbox1

In [ ]:
videos = os.listdir(videos_dir)
input_video = wg.Dropdown(options=videos,
                        value="Remo_Lite_480p.mp4",
                        description='Video:',
                        disabled=False)
model_nn = wg.Dropdown( options=["None", "Openpose Model"],
                        value="None",
                        description='Inference:',
                        disabled=False)
threshold = wg.FloatText(value=0.1, description='threshold:',disabled=False)
n_interp_samples = wg.IntText(value=10, description='n_interp_s:',disabled=False)
paf_score_th = wg.FloatText(value=0.1, description='paf_score_th:',disabled=False)
conf_th = wg.FloatText(value=0.7, description='conf_th:',disabled=False)
summary = wg.Text(value='',placeholder='description',description='Summary:',disabled=False)
output_name = wg.Text(
        value='',
        placeholder='File output name',
        description='Output:',
        disabled=False
    )
process_vid = wg.Button(description='Process Video')

def onProcessClicked(b):
    if(model_nn.value=='None'):
        print("Select inference method")
    elif(model_nn.value=='Openpose Model'):
        processVideo(input_video.value, threshold.value, n_interp_samples.value,
                     paf_score_th.value, conf_th.value, summary.value, output_name.value)
    else:
        print("Post processing not implemented yet")
        
process_vid.on_click(onProcessClicked)

vbox1 = wg.VBox([input_video, model_nn, threshold, n_interp_samples, paf_score_th, conf_th, summary, output_name, process_vid])
display(vbox1)

In [23]:
folder_files = os.listdir()

In [24]:
folder_files

['Openpose_analysis.ipynb',
 '.ipynb_checkpoints',
 'functions.py',
 'untitled.txt',
 'Teste.ipynb',
 'Interface.ipynb',
 'post_processing_template.py',
 'MPOP_video.py',
 'Results.ipynb',
 'Untitled.ipynb',
 '__pycache__',
 'Untitled1.ipynb']

In [26]:
py_list = []
for names in folder_files:
    if names.endswith(".py"):
        py_list.append(names)
print(py_list)

['functions.py', 'post_processing_template.py', 'MPOP_video.py']


In [2]:
t = wg.IntSlider(
    value=7,
    min=0,
    max=10,
    step=1,
    description='Test:',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)

In [3]:
def disp(v):
    display(v)

In [4]:
disp(t)

IntSlider(value=7, continuous_update=False, description='Test:', max=10)

In [1]:
import os

import ipywidgets as widgets


class FileBrowser(object):
    def __init__(self):
        self.path = os.getcwd()
        self._update_files()
        
    def _update_files(self):
        self.files = list()
        self.dirs = list()
        if(os.path.isdir(self.path)):
            for f in os.listdir(self.path):
                ff = self.path + "/" + f
                if os.path.isdir(ff):
                    self.dirs.append(f)
                else:
                    self.files.append(f)
        
    def widget(self):
        box = widgets.VBox()
        self._update(box)
        return box
    
    def _update(self, box):
        
        def on_click(b):
            if b.description == '..':
                self.path = os.path.split(self.path)[0]
            else:
                self.path = self.path + "/" + b.description
            self._update_files()
            self._update(box)
        
        buttons = []
        if self.files:
            button = widgets.Button(description='..', background_color='#d0d0ff')
            button.on_click(on_click)
            buttons.append(button)
        for f in self.dirs:
            button = widgets.Button(description=f, background_color='#d0d0ff')
            button.on_click(on_click)
            buttons.append(button)
        for f in self.files:
            button = widgets.Button(description=f)
            button.on_click(on_click)
            buttons.append(button)
        box.children = tuple([widgets.HTML("<h2>%s</h2>" % (self.path,))] + buttons)

In [ ]:

f = FileBrowser()
f.widget()
<interact with widget, select a path>
in a separate cell:
  f.path # returns the selected path